In [1]:
from manim import *

Manim Community v0.16.0

In [2]:
config.media_width = "100%"
config.media_embed = True

In [4]:
%%manim -qm -v WARNING E1

class E1(Scene):
	def construct(self):
		# Title
		fx_tex = MathTex("f(x)=x^2").scale(2)\
			.to_corner(UR)

		# Create sliders
		slider_kwargs = {"include_numbers": True}
		x_slider  = NumberLine(x_range=[0,10,1],length=7,**slider_kwargs)
		fx_slider = NumberLine(x_range=[0,100,10],length=12,**slider_kwargs)

		sliders_grp = VGroup(x_slider,fx_slider)\
			.arrange(DOWN,buff=2,aligned_edge=LEFT)\
			.to_edge(LEFT)

		# Create marks
		x_mark = Triangle(fill_opacity=1)\
			.set(height=0.2)\
			.flip(RIGHT)\
			.next_to(x_slider.n2p(0),UP,buff=0.03)
		fx_mark = x_mark.copy()
		fx_mark.next_to(fx_slider.n2p(0),UP,buff=0.03)\
			.set_color(RED)

		# Create DecimalNumber
		x_dn  = DecimalNumber(0)\
			.next_to(x_mark,UP,buff=0.1)
		fx_dn = x_dn.copy()
		fx_dn.next_to(fx_mark,UP,buff=0.1)

		# Add updaters
		x_dn.add_updater(lambda mob: mob.next_to(x_mark,UP,buff=0.1))
		fx_dn.add_updater(lambda mob: 
										mob.next_to(fx_mark,UP,buff=0.1)
										   .set_value(x_dn.get_value()**2)
		)
		x_mark.add_updater(lambda mob: mob.next_to(x_slider.n2p(x_dn.get_value()),UP,buff=0.03))
		fx_mark.add_updater(lambda mob: mob.next_to(fx_slider.n2p(fx_dn.get_value()),UP,buff=0.03))


		self.add(
			fx_tex,
			sliders_grp,
			x_mark,fx_mark,
			x_dn,fx_dn
		)
		self.wait()
		self.play(
			ChangeDecimalToValue(x_dn,3),
			run_time=3
		)
		self.wait()
		self.play(
			ChangeDecimalToValue(x_dn,1),
			run_time=2
		)
		self.wait()
		self.play(
			ChangeDecimalToValue(x_dn,10),
			run_time=5
		)
		self.wait()


In [5]:
%%manim -qm -v WARNING E2

class E2(Scene):
    def construct(self):
        A = 1
        B = 0
        C = 0

        equation = VGroup(
            MathTex(r"\cos(at)+{\cos(bt)\over 2}+{\sin(ct)\over 3}"),
            MathTex(r"\sin(at)+{\sin(bt)\over 2}+{\cos(ct)\over 3}")
        ).scale(0.9).arrange(DOWN,aligned_edge=LEFT)

        equation.to_corner(UR)

        brace = Brace(equation,LEFT)
        C_ = brace.get_tex("C")

        range_ = MathTex(r"t\in[0,2\pi]")
        range_.next_to(equation,DOWN).align_to(equation,RIGHT)

        values = VGroup(*[
            MathTex(f"{t}=",tex_to_color_map={f"{t}":color}).scale(1.3)
            for t,color in zip(["a","b","c"],[RED,BLUE,YELLOW])
        ])
        values.arrange(DOWN,aligned_edge=LEFT,buff=1.2)
        values.next_to(equation,DOWN,buff=1.4)
        values.align_to(equation,LEFT).shift(RIGHT*0.2)

        dn_kwargs = {"unit": r"^\circ"}
        D_A = DecimalNumber(A,**dn_kwargs)
        D_B = DecimalNumber(B,**dn_kwargs)
        D_C = DecimalNumber(C,**dn_kwargs)
        D_G = VGroup(D_A,D_B,D_C)
        for d,s in zip(D_G,values):
            d.next_to(s,aligned_edge=DOWN)

        axes = Axes(
        	x_range=[-2,2,1],
        	y_range=[-2,2,1],
        	x_length=4,
        	y_length=4
        )
        axes.shift(LEFT*3)

        pc = always_redraw(
        	lambda: self.get_param_func(
        		axes,
        		D_A.get_value(),
        		D_B.get_value(),
        		D_C.get_value()
        	)
        )

        self.wait(0.3)
        self.play(
        	Write(axes),
        	Create(pc),
            Write(equation),
            GrowFromCenter(brace),
            Write(C_),
            Write(range_)
        )
        self.wait(0.5)
        self.play(
            Write(values),
            Write(D_G),
        )
        self.wait(0.5)
        self.play(
            ChangeDecimalToValue(D_B,15),
            run_time=7,
            rate_func=linear,
        )
        self.wait(0.3)
        self.play(
            ChangeDecimalToValue(D_A,15),
            run_time=7,
            rate_func=linear,
        )
        self.wait(0.3)
        self.play(
            ChangeDecimalToValue(D_C,15),
            run_time=7,
            rate_func=linear,
        )
        self.wait(0.3)


    def get_param_func(self, axes, a, b, c):
        return axes.plot_parametric_curve(
            lambda t: np.array([
                np.cos(a * t) + np.cos(b * t) / 2 + np.sin(c * t) / 3,
                np.sin(a * t) + np.sin(b * t) / 2 + np.cos(c * t) / 3,
                0
            ]),
            t_range=[0,2*PI,0.007],
            color=RED
        )


In [6]:
%%manim -qm -v WARNING E3

class E3(Scene):
	def construct(self):
		func = lambda x: 0.1 * (x - 2) * (x - 8) * (x - 5) + 3
		axes = Axes(
			axis_config={"include_numbers": True},
			x_range=[-1,10,1],
			y_range=[-1,6,1]
		)
		plot = axes.plot(func,x_range=[0.8,9,0.01],color=RED)
		self.add(axes,plot)
		# Solution
		x_tr = ValueTracker(2)

		dot = always_redraw(
			lambda: Dot(
				axes.c2p(
					x_tr.get_value(),
					func(x_tr.get_value())
				),
				color=YELLOW
			)
		)
		lines = always_redraw(
			lambda: VGroup(
				axes.get_lines_to_point(dot.get_center())
			)
		)
		tangent = always_redraw(
			lambda: Line(LEFT,RIGHT,color=YELLOW)
				.set_angle(
					Line(
						# angle_of(p + dp)
						axes.c2p(x_tr.get_value()       ,func(x_tr.get_value())),
						axes.c2p(x_tr.get_value()+0.0001,func(x_tr.get_value()+0.0001)),
					).get_angle()
				)
				.move_to(dot.get_center())
		)

		self.add(dot,lines,tangent)
		self.play(
			x_tr.animate.set_value(8),
			run_time=8
		)
		self.wait()



In [7]:
%%manim -qm -v WARNING E4

class E4(Scene):
	def construct(self):
		init_points = [
			(-2,-2), # start
			(-2,2),  # handle 1
			(2,2),   # handle 2
			(2,-2)   # end
		]

		start = Dot([*init_points[0],0])
		handle1 = Dot([*init_points[1],0])
		handle2 = Dot([*init_points[2],0])
		end = Dot([*init_points[3],0])

		dots = [start,handle1,handle2,end]

		join_line = always_redraw(lambda: VMobject().set_points_as_corners(
			[d.get_center() for d in dots]
		))

		bezier_curve = always_redraw(
			# ParametricFunction is the same as
			# axes.plot_parametric_curve but
			# using the camera system as reference
			lambda: ParametricFunction(
					bezier(
						[d.get_center() for d in dots]
					),
					color=RED
				)
		)

		self.add(start,handle1,handle2,end,join_line,bezier_curve)
		self.wait()
		self.play(start.animate.shift(LEFT*2))
		self.wait()
		self.play(end.animate.shift(RIGHT*2))
		self.wait()
		self.play(
			start.animate.shift(UP*4),
			handle1.animate.shift(DOWN*4),
			run_time=3
		)
		self.wait()
		self.play(end.animate.shift(DL*1.5+LEFT))
		self.wait()


In [8]:
%%manim -qm -v WARNING E5

class E5(Scene):
	def construct(self):
		circle = Circle(radius=2,color=WHITE)\
			.rotate(90*DEGREES)\
			.flip(UP) # Why this? Try to remove it
		# self.add(Dot(circle.get_start())) # see that the start point is the top
		minutes_ticks = VGroup(*[
			Line(
				circle.get_center(),
				circle.point_from_proportion(i/60)
			).get_subcurve(0.89 if i%5==0 else 0.965,1)
			for i in range(60)
		])

		hours = [12,*range(1,12)]

		hours_tex = VGroup(*[
			MathTex(h)
				.set(height=0.3)
				.move_to(
				Line(
					circle.get_center(),
					circle.point_from_proportion(i/12)
				).point_from_proportion(0.8)
			)
			for h,i in zip(hours,range(12))
		])
		# 							  hours + minutes
		hour_tr = ComplexValueTracker(2+30j)

		hour_arrow = always_redraw(
			lambda: Arrow(
				circle.get_center(),
				circle.point_from_proportion(
					((hour_tr.get_value().real+hour_tr.get_value().imag/60)%12)/12
				),
				buff=0,
				color=RED
			).scale(0.7,about_point=circle.get_center())
		)

		minute_arrow = always_redraw(
			lambda: Arrow(
				circle.get_center(),
				circle.point_from_proportion(
					((hour_tr.get_value().imag)%60)/60
				),
				buff=0,
				color=BLUE
			).scale(0.9,about_point=circle.get_center())
		)

		self.add(circle, minutes_ticks, hour_arrow, minute_arrow, hours_tex)
		# 			4 hours  + 40 minutes 
		increment = 4 * (60) + 40
		# So, if initial: 2h+30min then 2h+30min + 4h+40min = 7h+10min

		self.play(
			hour_tr.animate.increment_value(complex(0,increment)),
			run_time=12,
			rate_func=linear
		)
		self.wait()


In [9]:
%%manim -qm -v WARNING E6

class E6(Scene):
	def construct(self):
		func = lambda x: 0.1 * (x - 2) * (x - 8) * (x - 5) + 3
		axes = Axes(
			axis_config={"include_numbers": True},
			x_range=[-1,10,1],
			y_range=[-1,6,1]
		)
		plot = axes.plot(func,x_range=[0.8,9,0.01],color=RED)
		slider_tr = ValueTracker(4)
		slider = always_redraw(
			lambda: axes.get_T_label(x_val=slider_tr.get_value(),graph=plot)
		)
		area = always_redraw(
			lambda: axes.get_riemann_rectangles(
				plot,
				x_range=[2,slider_tr.get_value()],
				dx=0.01,
				stroke_width=1,
			).set_color_by_gradient(GREEN,TEAL)
		)
		# Animations
		self.add(axes,plot,area,slider)
		self.wait()
		self.play(
			slider_tr.animate.set_value(8),
			run_time=3
		)
		self.wait()
		self.play(
			slider_tr.animate.set_value(6),
			run_time=3
		)
		self.wait()
		self.play(
			slider_tr.animate.set_value(8.5),
			run_time=3
		)
		self.wait()

In [10]:
%%manim -qm -v WARNING E7

class E7(Scene):
    def get_circle(self, plot, axes, vt, focus):
        proportion_coord = axes.i2gp(vt.get_value(),plot)
        radius = proportion_coord[1] - axes.x_axis.n2p(vt.get_value())[1]
        circle = Circle(radius=radius,arc_center=proportion_coord)
        dot = Dot(circle.get_center(),color=RED)
        circle.add(axes.get_vertical_line(circle.get_center()))
        circle.add(DashedLine(circle.get_center(),focus))
        circle.add(dot)
        return circle

    def construct(self):
        axes = Axes(
            x_range=[-6,6,1],
            y_range=[0,7,1],
            x_length=12,
            y_length=7,
            axis_config={
                "include_ticks": False,
                "include_tip": False
            }
        )
        axes.to_edge(DOWN)

        h = 0; k = 1; p = 1

        parabola_func = lambda x: ((x-h)**2)/(4*p) + k

        left_plot = axes.plot(parabola_func, x_range=[-5,0,0.01])
        left_plot.reverse_points()
        right_plot = axes.plot(parabola_func, x_range=[0,5,0.01])

        focus = axes.c2p(0,2)
        right_vt = ValueTracker(0)
        left_vt = ValueTracker(0)

        # right_circle = self.get_circle(left_plot,axes,right_vt,focus)
        right_circle = always_redraw(lambda: self.get_circle(right_plot,axes,right_vt,focus))
        left_circle  = always_redraw(lambda: self.get_circle(left_plot,axes,left_vt,focus))

        self.add(
                axes,
                # left_plot,right_plot,
                right_circle,
                left_circle,
        )
        self.wait()
        self.bring_to_back(left_plot,right_plot)
        self.play(
            right_vt.animate.set_value(5),
            left_vt.animate.set_value(-5),
            Create(left_plot),
            Create(right_plot),
            run_time=7
         )
        self.wait()


In [14]:
%%manim -qm -v WARNING E8

class E8(Scene):
    def construct(self):
        circle = Circle().scale(3)
        vt = ValueTracker(3)

        polygon = always_redraw(
            lambda: Polygon(*[
                circle.point_from_proportion(i/vt.get_value())
                for i in range(int(np.ceil(vt.get_value())))
            ])
        )
        self.add(polygon)
        self.wait(0.5)
        self.play(
            vt.animate.set_value(60),
            run_time=30,
            rate_func=linear,
        )
        self.wait()


In [15]:
%%manim -qm -v WARNING E9

class E9(Scene):
    def construct(self):
        dot  = Dot(color=RED)
        text = Text("Text")

        text.next_to(dot,DOWN)
        anim_kwargs = {"run_time": 3, "rate_func": linear}

        self.add(dot,text)
        self.wait()
        self.play(dot.animate.shift(RIGHT*3),**anim_kwargs)
        self.play(Rotate(dot,PI,about_point=ORIGIN,**anim_kwargs))
        self.play(Rotate(dot,-PI,about_point=ORIGIN,**anim_kwargs))
        self.wait()

In [16]:
%%manim -qm -v WARNING E10

class E10(Scene):
    def construct(self):
        dot  = Dot(color=RED)
        text = Text("Text")

        text.next_to(dot,DOWN)
        anim_kwargs = {"run_time": 3, "rate_func": linear}

        # updater definition
        def my_first_updater(mob):
            mob.next_to(dot,DOWN)
        # add updater to mobject
        text.add_updater(my_first_updater)

        self.add(dot,text)
        self.wait()
        self.play(dot.animate.shift(RIGHT*3),**anim_kwargs)
        self.play(Rotate(dot,PI,about_point=ORIGIN,**anim_kwargs))
        self.play(Rotate(dot,-PI,about_point=ORIGIN,**anim_kwargs))
        self.wait()

In [17]:
%%manim -qm -v WARNING E11

class E11(Scene):
    def construct(self):
        dot  = Dot(color=RED)
        text = Text("Text")

        text.next_to(dot,DOWN)
        anim_kwargs = {"run_time": 3, "rate_func": linear}

        # updater definition
        def my_first_updater(mob):
            mob.next_to(dot,DOWN)
        # add updater to mobject
        text.add_updater(my_first_updater)

        self.add(dot,text)
        self.wait()
        self.play(dot.animate.shift(RIGHT*3),**anim_kwargs)
        self.play(Rotate(dot,PI,about_point=ORIGIN,**anim_kwargs))
        # remove all updaters:
        text.clear_updaters()
        self.play(Rotate(dot,-PI,about_point=ORIGIN,**anim_kwargs))
        self.wait()

In [18]:
%%manim -qm -v WARNING E12

class E12(Scene):
    def construct(self):
        dot  = Dot(color=RED)
        text = Text("Text")

        text.next_to(dot,DOWN)
        anim_kwargs = {"run_time": 3, "rate_func": linear}

        # updater definition
        def my_first_updater(mob):
            mob.next_to(dot,DOWN)
        # add updater to mobject
        text.add_updater(my_first_updater)

        self.add(dot,text)
        self.wait()
        self.play(dot.animate.shift(RIGHT*3),**anim_kwargs)
        text.suspend_updating()
        self.play(Rotate(dot,PI,about_point=ORIGIN,**anim_kwargs))
        text.resume_updating()
        self.play(Rotate(dot,-PI,about_point=ORIGIN,**anim_kwargs))
        self.wait()

In [19]:
%%manim -qm -v WARNING E13

class E13(Scene):
    def construct(self):
        dot  = Dot(color=RED)
        text = Text("Text")

        text.next_to(dot,DOWN)
        anim_kwargs = {"run_time": 3, "rate_func": linear}

        # updater definition
        def my_first_updater(mob):
            mob.next_to(dot,DOWN)

        self.add(dot,text)
        self.wait()
        self.play(
            dot.animate.shift(RIGHT*3),
            UpdateFromFunc(text,my_first_updater),
            **anim_kwargs
        )
        self.play(Rotate(dot,PI,about_point=ORIGIN,**anim_kwargs))
        self.play(
            Rotate(dot,-PI,about_point=ORIGIN,**anim_kwargs),
            UpdateFromFunc(text,my_first_updater),
        )
        self.wait()

In [20]:
%%manim -qm -v WARNING E14

class E14(Scene):
    def construct(self):
        dot  = Dot(color=RED)
        text = Text("Text")

        text.next_to(dot,DOWN)
        anim_kwargs = {"run_time": 3, "rate_func": linear}

        text.add_updater(
            lambda mob: mob.next_to(dot,DOWN)
        )

        self.add(dot,text)
        self.wait()
        self.play(dot.animate.shift(RIGHT*3),**anim_kwargs)
        self.play(Rotate(dot,PI,about_point=ORIGIN,**anim_kwargs))
        self.play(Rotate(dot,-PI,about_point=ORIGIN,**anim_kwargs))
        self.wait()

In [21]:
%%manim -qm -v WARNING E15

class E15(Scene):
    def construct(self):
        dot    = Dot(color=RED)
        text   = Text("Text")
        square = Square()

        text.next_to(dot,DOWN)
        anim_kwargs = {"run_time": 3, "rate_func": linear}

        text.add_updater(
            lambda mob: mob.next_to(dot,DOWN)
        )
        square.add_updater(
            lambda mob: mob.next_to(dot,LEFT)
        )

        self.add(dot,square,text)
        self.wait()
        self.play(dot.animate.shift(RIGHT*3),**anim_kwargs)
        self.play(Rotate(dot,PI,about_point=ORIGIN,**anim_kwargs))
        self.play(Rotate(dot,-PI,about_point=ORIGIN,**anim_kwargs))
        self.wait()

In [22]:
%%manim -qm -v WARNING E16

class E16(Scene):
    def construct(self):
        dot    = Dot(color=RED)
        text   = Text("Text")
        square = Square()

        text.next_to(dot,DOWN)
        anim_kwargs = {"run_time": 3, "rate_func": linear}

        def my_closure(direction):
            def my_updater(mob):
                mob.next_to(dot,direction)
            return my_updater

        text.add_updater(my_closure(RIGHT))
        square.add_updater(my_closure(UP))

        self.add(dot,square,text)
        self.wait()
        self.play(dot.animate.shift(RIGHT*3),**anim_kwargs)
        self.play(Rotate(dot,PI,about_point=ORIGIN,**anim_kwargs))
        self.play(Rotate(dot,-PI,about_point=ORIGIN,**anim_kwargs))
        self.wait()

In [23]:
%%manim -qm -v WARNING E17

class E17(Scene):
    def my_closure(self, dot, direction):
        def _updater(mob):
            mob.next_to(dot,direction)
        return _updater

    def construct(self):
        dot    = Dot(color=RED)
        text   = Text("Text")
        square = Square()

        text.next_to(dot,DOWN)
        anim_kwargs = {"run_time": 3, "rate_func": linear}

        text.add_updater(self.my_closure(dot,RIGHT))
        square.add_updater(self.my_closure(dot,DOWN))

        self.add(dot,square,text)
        self.wait()
        self.play(dot.animate.shift(RIGHT*3),**anim_kwargs)
        self.play(Rotate(dot,PI,about_point=ORIGIN,**anim_kwargs))
        self.play(Rotate(dot,-PI,about_point=ORIGIN,**anim_kwargs))
        self.wait()

In [24]:
%%manim -qm -v WARNING E18

class E18(Scene):
    def construct(self):
        t = Text("Text")
        c = Circle()
        s = Square()

        self.add(t)
        self.wait()
        # old versions: Transform(t,c).update()
        t.become(c)
        self.wait()
        t.become(s)
        self.wait()
        t.set_color(RED)
        self.wait()

In [25]:
%%manim -qm -v WARNING E19

class E19(Scene):
    def construct(self):
        line  = Line(LEFT*3,RIGHT*3)
        brace = Brace(
            line,
            rotate_vector(line.get_unit_vector(),PI/2)
        )

        anim_kwargs = {"run_time": 2, "rate_func": linear}
        self.add(line,brace)
        self.wait(0.5)
        self.play(line.animate.set_length(2),**anim_kwargs)
        self.wait(0.5)
        self.play(Rotate(line,PI/2,**anim_kwargs))
        self.wait(0.5)
        self.play(line.animate.shift(DOWN),**anim_kwargs)
        self.wait()

In [26]:
%%manim -qm -v WARNING E20

class E20(Scene):
    def construct(self):
        line  = Line(LEFT*3,RIGHT*3)
        brace = Brace(
            line,
            rotate_vector(line.get_unit_vector(),PI/2)
        )

        # define updater
        def brace_updater(mob):
            new_brace = Brace(
                    line,
                    rotate_vector(line.get_unit_vector(),PI/2)
                )
            mob.become(new_brace)

        brace.add_updater(brace_updater)

        anim_kwargs = {"run_time": 2, "rate_func": linear}
        self.add(line,brace)
        self.wait(0.5)
        self.play(line.animate.set_length(2),**anim_kwargs)
        self.wait(0.5)
        self.play(Rotate(line,PI/2,**anim_kwargs))
        self.wait(0.5)
        self.play(line.animate.shift(DOWN),**anim_kwargs)
        self.wait()

In [27]:
%%manim -qm -v WARNING E21

class E21(Scene):
    def construct(self):
        line  = Line(LEFT*3,RIGHT*3)

        # always_redraw already set the updater to the object.
        brace = always_redraw(
            lambda: Brace(
                            line,
                            rotate_vector(line.get_unit_vector(),PI/2)
                        )
        )

        anim_kwargs = {"run_time": 2, "rate_func": linear}
        self.add(line,brace)
        self.wait(0.5)
        self.play(line.animate.set_length(2),**anim_kwargs)
        self.wait(0.5)
        self.play(line.animate.shift(DOWN),**anim_kwargs)
        self.wait(0.5)
        self.play(Rotate(line,-PI/2,**anim_kwargs))
        self.wait()

In [28]:
%%manim -qm -v WARNING E22

class E22(Scene):
    def construct(self):
        number_line = NumberLine(x_range=[-5,5,1],length=10,include_numbers=True)
        INITIAL_VALUE = -2
        vt = ValueTracker(INITIAL_VALUE)

        t = always_redraw(
            lambda: Triangle(fill_opacity=1)
                        .rotate(PI)
                        .set(height=0.4)
                        .next_to(number_line.n2p(vt.get_value()),UP,buff=0)
        )

        self.add(number_line,t)
        self.wait()
        self.play( vt.animate.set_value(-5), run_time=3 )
        self.wait()
        self.play( vt.animate.increment_value(5), run_time=3 )
        self.wait()
        self.play( vt.animate.set_value(3), run_time=3 )
        self.wait()

In [29]:
%%manim -qm -v WARNING E23

class E23(Scene):
    def construct(self):
        theta = ValueTracker(20*DEGREES)

        line1 = Line(LEFT*2,RIGHT*2)
        line2 = always_redraw(
            lambda: line1.copy()
                        .set_angle(theta.get_value()) # <- Set the angle
                        .set_color(RED)
        )
        angle = always_redraw(
            lambda: Angle(line1,line2,other_angle=False if theta.get_value() > 0 else True)
        )

        self.add(line1,line2,angle)
        self.wait(0.5)
        self.play(
            theta.animate.set_value(90*DEGREES),
            run_time=2.5
        )
        self.wait(0.5)
        self.play(
            theta.animate.increment_value(-120*DEGREES),
            run_time=2.5
        )
        self.wait(0.5)

In [32]:
%%manim -qm -v WARNING E24

class MyScene(Scene):
    def setup(self):
        self.np = NumberPlane(axis_config={"include_numbers":True})
        self.add(self.np)

class E24(MyScene):
    def construct(self):
        coord = ComplexValueTracker(0+0j)

        dot = always_redraw(
            lambda: Dot([
                coord.get_value().real,
                coord.get_value().imag,
                0
        ]))

        self.add(dot)
        self.wait()
        self.play(coord.animate.set_value(1+0j)) # (1,0)
        self.wait()
        self.play(coord.animate.set_value(1+2j)) # (1,2)
        self.wait()
        self.play(coord.animate.increment_value(1-1j)) # (1,2) + (1,-1) = (2,1)
        self.wait()

In [33]:
%%manim -qm -v WARNING E25

class E25(MyScene):
    def construct(self):
        coord = ComplexValueTracker(0+0j)

        dot = always_redraw(
            lambda: Dot([complex_to_R3(coord.get_value())],color=RED))

        self.add(NumberPlane(), dot)
        self.wait()
        self.play(coord.animate.set_value(1+0j))
        self.wait()
        self.play(coord.animate.set_value(1+2j))
        self.wait()
        self.play(coord.animate.increment_value(1-1j))
        self.wait()

In [34]:
%%manim -qm -v WARNING E26

class E26(Scene):
    def construct(self):
        nl = NumberLine(include_numbers=True)
        selector = Triangle(fill_opacity=1,color=RED).scale(0.2).rotate(PI/3)
        dn = DecimalNumber(0)

        update_grp = VGroup(selector, dn)

        def update_vgrp(vgrp):
            s,d = vgrp
            s.next_to(nl.n2p(dn.get_value()),UP,buff=0)
            d.next_to(selector,UP,buff=0.1)

        update_grp.add_updater(update_vgrp)

        self.add(nl,update_grp) # <-- add grp complete, not each element
        # Not use self.add(nl, selecttor, dn)
        self.wait(0.5)
        self.play( ChangeDecimalToValue(dn, 4), run_time=2 )
        self.wait(0.5)
        self.play( ChangeDecimalToValue(dn, -1), run_time=2 )
        self.wait(0.5)
        self.play( ChangeDecimalToValue(dn, -4), run_time=2 )
        self.wait(0.5)
        self.play( ChangeDecimalToValue(dn, 7), run_time=3 )
        self.wait(0.5)

In [13]:
%%manim -qm -v WARNING E27

class E27(Scene):
    def construct(self):
        theta = DecimalNumber(20,num_decimal_places=1,unit="^\\circ")

        line1 = Line(LEFT*2,RIGHT*2)
        line2 = always_redraw(
            lambda: line1.copy()
                        .set_angle(theta.get_value()*DEGREES) # <- Set the angle
                        .set_color(RED)
        )
        angle = always_redraw(
            lambda: Angle(
                line1,line2,
                radius=3,
                other_angle=False if theta.get_value()*DEGREES > 0 else True
            )
        )
        theta.next_to(line1,LEFT,buff=1)
        self.add(theta,line1,line2,angle)
        self.wait(0.5)
        self.play( # theta.animate.set_value(90*DEGREES),
            ChangeDecimalToValue(theta,90), run_time=2.5
        )
        self.wait(0.5)
        self.play( # theta.animate.increment_value(-120*DEGREES),
            ChangeDecimalToValue(theta,-30), run_time=2.5
        )
        self.wait(0.5)

In [35]:
%%manim -qm -v WARNING E28

class E28(Scene):
    def construct(self):
        dot = Dot(color=RED)
        square = always_redraw(lambda: Square().next_to(dot,DOWN))
        circle = always_redraw(lambda: Circle().move_to(square,DOWN))

        self.add(dot,circle,square)
        print(self.mobjects)
        self.wait(0.5)
        self.play(dot.animate.shift(RIGHT*3),run_time=3)
        self.wait(0.5)
        self.play(dot.animate.shift(LEFT*6),run_time=5)
        self.wait(0.5)
        self.play(dot.animate.move_to(ORIGIN).to_edge(UP),run_time=3)
        self.wait(0.5)

[Dot, Circle, Square]


In [31]:
%%manim -qm -v WARNING E29

class E29(Scene):
    def construct(self):
        d = Dot(color=RED)
        c = Circle()
        s = Square()
        grp = VGroup(c,s)

        def grp_updater(_grp):
            _c,_s = _grp
            _c.next_to(d,LEFT)
            _s.next_to(d,RIGHT)
        grp.add_updater(grp_updater)

        # self.add(d,grp)
        # Don't use:
        self.add(d, c, s)
        anim_kwargs = {"run_time": 3, "rate_func": linear}
        self.wait(0.5)
        self.play(d.animate.shift(RIGHT*3),**anim_kwargs)
        self.play(Rotate(d,PI,about_point=ORIGIN,**anim_kwargs))
        self.play(Rotate(d,-PI,about_point=ORIGIN,**anim_kwargs))
        self.wait()